# <span style="color: purple; background-color: None; font-size: 36px; font-weight: bold; font-style: italic;"> Problem Statement  </span>

A retail chain wants to predict the demand for all SKU's at its 76 different stores. The available historical data is for the past 3 years. The frecasting horizon is the next 12 weeks.

First, I import all the libraries needed for this project:

In [1]:
#The Yoozh:
import numpy as np
import pandas as pd
import seaborn as sns

#Plotting:
import matplotlib.pyplot as plt
import plotly.express as px
from IPython.display import HTML # HTML display function
import plotly.io as pio
pio.renderers.default = "kaggle"
import plotly.graph_objects as go
from plotly.graph_objects import FigureWidget
from plotly.subplots import make_subplots
import ipywidgets as widgets
from ipywidgets import HBox, VBox, interactive_output
from statsmodels.tsa.stattools import acf, pacf
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf

#Time
from datetime import datetime as datetime
from datetime import timedelta
import time
from tqdm import tqdm
import holidays

from category_encoders import MEstimateEncoder

from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV, TimeSeriesSplit
import optuna

#Models
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
import lightgbm as lgb
from lightgbm import LGBMRegressor
import xgboost as xgb 

#Logistics
import warnings
import os
from pathlib import Path
import random
random_seed = 0
random.seed(random_seed)
np.random.seed(random_seed)

*Importing the Data:*

In [2]:
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

/kaggle/input/demand-forecasting/test_nfaJ3J5.csv
/kaggle/input/demand-forecasting/train_0irEZ2H.csv
/kaggle/input/demand-forecasting/sample_submission_pzljTaX.csv


In [3]:
train = pd.read_csv('/kaggle/input/demand-forecasting/train_0irEZ2H.csv')
test = pd.read_csv('/kaggle/input/demand-forecasting/test_nfaJ3J5.csv')
submit = pd.read_csv('/kaggle/input/demand-forecasting/sample_submission_pzljTaX.csv')

# <span style="color: purple; background-color: None; font-size: 36px; font-weight: bold; font-style: italic;"> EDA </span>

In [4]:
train.head()

record_ID      week  store_id  sku_id  total_price  base_price  \
0          1  17/01/11      8091  216418      99.0375    111.8625   
1          2  17/01/11      8091  216419      99.0375     99.0375   
2          3  17/01/11      8091  216425     133.9500    133.9500   
3          4  17/01/11      8091  216233     133.9500    133.9500   
4          5  17/01/11      8091  217390     141.0750    141.0750   

   is_featured_sku  is_display_sku  units_sold  
0                0               0          20  
1                0               0          28  
2                0               0          19  
3                0               0          44  
4                0               0          52

In [5]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 150150 entries, 0 to 150149
Data columns (total 9 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   record_ID        150150 non-null  int64  
 1   week             150150 non-null  object 
 2   store_id         150150 non-null  int64  
 3   sku_id           150150 non-null  int64  
 4   total_price      150149 non-null  float64
 5   base_price       150150 non-null  float64
 6   is_featured_sku  150150 non-null  int64  
 7   is_display_sku   150150 non-null  int64  
 8   units_sold       150150 non-null  int64  
dtypes: float64(2), int64(6), object(1)
memory usage: 10.3+ MB


Week column has data type object, which needs to be changed to dateTime. Moreover, there is a missing value for total_price column. I fill it with its corresponding base_price value.

In [6]:
train['week'] = pd.to_datetime(train['week'], format = '%d/%m/%y')
fill_value = train[train['total_price'].isnull()]['base_price']
train['total_price']=train['total_price'].fillna(fill_value)

In [7]:
train.describe()

record_ID                           week       store_id  \
count  150150.000000                         150150  150150.000000   
mean   106271.555504  2012-04-13 01:06:27.692307712    9199.422511   
min         1.000000            2011-01-17 00:00:00    8023.000000   
25%     53111.250000            2011-08-29 00:00:00    8562.000000   
50%    106226.500000            2012-04-13 12:00:00    9371.000000   
75%    159452.750000            2012-11-27 00:00:00    9731.000000   
max    212644.000000            2013-07-09 00:00:00    9984.000000   
std     61386.037861                            NaN     615.591445   

              sku_id    total_price     base_price  is_featured_sku  \
count  150150.000000  150150.000000  150150.000000    150150.000000   
mean   254761.132468     206.628502     219.425927         0.095611   
min    216233.000000      41.325000      61.275000         0.000000   
25%    217217.000000     130.387500     133.237500         0.000000   
50%    222087.000000     198.075000     205.912500         0.000000   
75%    245338.000000     233.700000     234.412500         0.000000   
max    679023.000000     562.162500     562.162500         1.000000   
std     85547.306447     103.310400     110.961712         0.294058   

       is_display_sku     units_sold  
count   150150.000000  150150.000000  
mean         0.133200      51.674206  
min          0.000000       1.000000  
25%          0.000000      20.000000  
50%          0.000000      35.000000  
75%          0.000000      62.000000  
max          1.000000    2876.000000  
std          0.339792      60.207904

Based on this description, we need to address two possible issues:
1. Record_ID maximum is much larger than the count of it, indicating that record_Id's are not being incremented by 1 consistently, and moreover, for the prediction itself, we dont need record_ID, so we might be tempted to drop it; and we would but for the fact that our submission csv file dataframe has a record_ID column that needs to stay coherent with our data. So we keep it.
2. In units_sold description, a stark contrast is observed between 75% percentile and maximum values, signaling the presence of outliers. To better understand the distribution of units_sold in our dataset we plot its histogram:

In [8]:
fig = px.histogram(train,
                   x="units_sold",
                   title='Distribution of Units Sold',
                   labels={'units_sold': 'Units Sold'},
                   nbins=50,
                   template='plotly_white',
                   color_discrete_sequence=['#636EFA'])
fig.update_layout(
    xaxis_title_text='Units Sold',
    yaxis_title_text='Frequency',
    bargap=0.1,
    title_x=0.5,
    width=600,
    height=400
)
fig.show()

The data is right skewed! But as it has a semi-log-normal distribution, we might still be able to use all data vailable to us, but we need to explore more:

In [9]:
x_transformed = np.log1p(train['units_sold'])

fig = px.histogram(x=x_transformed,
                   title='Distribution of Log(1 + Units Sold)',
                   labels={'x': 'Log(1 + Units Sold)'}, 
                   nbins=50,
                   template='plotly_white',
                   color_discrete_sequence=['#636EFA'])
fig.update_layout(
    xaxis_title_text='Log(1 + Units Sold)', 
    yaxis_title_text='Frequency',
    bargap=0.1,
    title_x=0.5,
    width=600,
    height=400
)
fig.show()

Since log1p of units_sold shows a normal distribution, I will use this transformed value in building the prediction model; and I can use all of the data, eliminating the need for dropping outliers. At the end, I will simply need to transform the predictions back to their original scale by using the function np.exp1m().

Let's look into the test dataframe as well:

In [10]:
test.head()

record_ID      week  store_id  sku_id  total_price  base_price  \
0     212645  16/07/13      8091  216418     108.3000    108.3000   
1     212646  16/07/13      8091  216419     109.0125    109.0125   
2     212647  16/07/13      8091  216425     133.9500    133.9500   
3     212648  16/07/13      8091  216233     133.9500    133.9500   
4     212649  16/07/13      8091  217390     176.7000    176.7000   

   is_featured_sku  is_display_sku  
0                0               0  
1                0               0  
2                0               0  
3                0               0  
4                0               0

In [11]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13860 entries, 0 to 13859
Data columns (total 8 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   record_ID        13860 non-null  int64  
 1   week             13860 non-null  object 
 2   store_id         13860 non-null  int64  
 3   sku_id           13860 non-null  int64  
 4   total_price      13860 non-null  float64
 5   base_price       13860 non-null  float64
 6   is_featured_sku  13860 non-null  int64  
 7   is_display_sku   13860 non-null  int64  
dtypes: float64(2), int64(5), object(1)
memory usage: 866.4+ KB


It is observed that the week column in test dataframe has the same Dtype issue, so we convert it to dateTime:

In [12]:
test['week'] = pd.to_datetime(test['week'], format = '%d/%m/%y')
test.head()

record_ID       week  store_id  sku_id  total_price  base_price  \
0     212645 2013-07-16      8091  216418     108.3000    108.3000   
1     212646 2013-07-16      8091  216419     109.0125    109.0125   
2     212647 2013-07-16      8091  216425     133.9500    133.9500   
3     212648 2013-07-16      8091  216233     133.9500    133.9500   
4     212649 2013-07-16      8091  217390     176.7000    176.7000   

   is_featured_sku  is_display_sku  
0                0               0  
1                0               0  
2                0               0  
3                0               0  
4                0               0

Let's look at the end of the train dataframe to make sure the dates in test dataset are the continuation of the train's:

In [13]:
train.tail()

record_ID       week  store_id  sku_id  total_price  base_price  \
150145     212638 2013-07-09      9984  223245     235.8375    235.8375   
150146     212639 2013-07-09      9984  223153     235.8375    235.8375   
150147     212642 2013-07-09      9984  245338     357.6750    483.7875   
150148     212643 2013-07-09      9984  547934     141.7875    191.6625   
150149     212644 2013-07-09      9984  679023     234.4125    234.4125   

        is_featured_sku  is_display_sku  units_sold  
150145                0               0          38  
150146                0               0          30  
150147                1               1          31  
150148                0               1          12  
150149                0               0          15

Let's now look at the correlation matrix of the train dataframe:

In [14]:
cols = [
    'base_price', 'total_price', 'is_featured_sku', 'is_display_sku', 'units_sold'
]

corr_matrix = train[cols].corr()

fig = px.imshow(
    corr_matrix,
    text_auto=True,
    aspect="auto",
    labels=dict(color="Correlation"),
    title='Feature Correlation Matrix',
    color_continuous_scale='RdBu_r'
)
fig.update_layout(
    title_x=0.5,
    width=650,
    height=650
)
fig.show()

The positive correlations of featuring and displaying, and the negative correlations of prices with units_sold make sense. That is an indicator of good data so far. 

Since the correlations of prices are not as large as we would want, we will engineer new features based on them in the next section. There, we will also assess the impact of features on our Baseline model.

# <span style="color: purple; background-color: None; font-size: 36px; font-weight: bold; font-style: italic;"> Feature Engineering  </span>

<span style="color:#003366; background-color:#F0F8FF; font-size: 26px; font-weight: bold; font-style: italic;"> Price Features  </span>

Since we have two different prices, engineering such features as price difference/relative-difference might reveal hidden information about discount on some SKU's:

In [15]:
train['diff'] = train['base_price'] - train['total_price']
train['relative_diff_total'] = train['diff']/train['total_price']
train['relative_diff_base'] = train['diff']/train['base_price']
test['diff'] = test['base_price'] - test['total_price']
test['relative_diff_total'] = test['diff']/test['total_price']
test['relative_diff_base'] = test['diff']/test['base_price']

cols = [
    'base_price', 'total_price', 'diff', 'relative_diff_base', 'relative_diff_total',
    'is_featured_sku', 'is_display_sku', 'units_sold'
]

corr_matrix = train[cols].corr()

fig = px.imshow(
    corr_matrix,
    text_auto=True,
    aspect="auto",
    labels=dict(color="Correlation"),
    title='Feature Correlation Matrix',
    color_continuous_scale='RdBu_r'
)
fig.update_layout(
    title_x=0.5,
    width=800,
    height=800
)
fig.show()

Indeed, diff and relative_diff's have high positive correlations with the units_sold. And they must have revealed some info about discount. So we keep these features, and solidify this current set of features as our baseline features.

<span style="color:#003366; background-color:#F0F8FF; font-size: 26px; font-weight: bold; font-style: italic;"> Basic Time Features  </span>

First, we extract basic time features as follows thus:

In [16]:
combined_df = pd.concat([train, test], ignore_index=True)

combined_df['weekend_date'] = combined_df['week'] + pd.to_timedelta(6, unit='D')

def extract_time_features (df):
    start_date = df['week'].min()
    df['year'] = df['week'].dt.year
    df['end_year'] = df['weekend_date'].dt.year
    
    df['quarter'] = df['week'].dt.quarter

    df['month'] = df['week'].dt.month
    df['month_sin'] = np.sin(2 * np.pi * df['month']/12)
    df['month_cos'] = np.cos(2 * np.pi * df['month']/12)
    df['end_month'] = df['weekend_date'].dt.month
    df['end_month_sin'] = np.sin(2 * np.pi * df['end_month']/12)
    df['end_month_cos'] = np.cos(2 * np.pi * df['end_month']/12)
    df['is_month_start'] = df['week'].dt.is_month_start.astype(int)
    df['is_month_end'] = df['week'].dt.is_month_end.astype(int)
    
    df['weeknum'] = df['week'].dt.isocalendar().week.astype(int)
    df['weeknum_sin'] = np.sin(2 * np.pi * df['weeknum']/52)
    df['weeknum_cos'] = np.cos(2 * np.pi * df['weeknum']/52)
    df['week_from_start'] = (df['week']-start_date).dt.days//7 
    
    df['day'] = df['week'].dt.day
    df['weekday'] = df['week'].dt.dayofweek
    
    return df
combined_df = extract_time_features(combined_df)

In [17]:
pd.set_option('display.max_columns', None)
combined_df.describe()

record_ID                           week       store_id  \
count  164010.000000                         164010  164010.000000   
mean   116090.309664  2012-05-25 02:01:41.408450560    9199.422511   
min         1.000000            2011-01-17 00:00:00    8023.000000   
25%     57989.250000            2011-09-19 00:00:00    8562.000000   
50%    116054.500000            2012-05-25 12:00:00    9371.000000   
75%    174176.750000            2013-01-29 00:00:00    9731.000000   
max    232287.000000            2013-10-01 00:00:00    9984.000000   
std     67059.235114                            NaN     615.591271   

              sku_id    total_price     base_price  is_featured_sku  \
count  164010.000000  164010.000000  164010.000000    164010.000000   
mean   254761.132468     207.098393     219.805933         0.094848   
min    216233.000000      41.325000      61.275000         0.000000   
25%    217217.000000     130.387500     133.237500         0.000000   
50%    222087.000000     198.787500     208.050000         0.000000   
75%    245338.000000     234.412500     235.837500         0.000000   
max    679023.000000     562.162500     562.162500         1.000000   
std     85547.282373     102.501242     110.351869         0.293006   

       is_display_sku     units_sold           diff  relative_diff_total  \
count   164010.000000  150150.000000  164010.000000        164010.000000   
mean         0.133211      51.674206      12.707540             0.067503   
min          0.000000       1.000000    -106.875000            -0.340000   
25%          0.000000      20.000000       0.000000             0.000000   
50%          0.000000      35.000000       0.000000             0.000000   
75%          0.000000      62.000000       0.000000             0.000000   
max          1.000000    2876.000000     250.800000             4.672414   
std          0.339804      60.207904      31.370528             0.161785   

       relative_diff_base                   weekend_date           year  \
count       164010.000000                         164010  164010.000000   
mean             0.048304  2012-05-31 02:01:41.408450816    2011.929577   
min             -0.515152            2011-01-23 00:00:00    2011.000000   
25%              0.000000            2011-09-25 00:00:00    2011.000000   
50%              0.000000            2012-05-31 12:00:00    2012.000000   
75%              0.000000            2013-02-04 00:00:00    2013.000000   
max              0.823708            2013-10-07 00:00:00    2013.000000   
std              0.102157                            NaN       0.792999   

            end_year        quarter          month     month_sin  \
count  164010.000000  164010.000000  164010.000000  1.640100e+05   
mean     2011.936620       2.394366       6.133803  2.370440e-02   
min      2011.000000       1.000000       1.000000 -1.000000e+00   
25%      2011.000000       1.000000       3.000000 -8.660254e-01   
50%      2012.000000       2.000000       6.000000  1.224647e-16   
75%      2013.000000       3.000000       9.000000  8.660254e-01   
max      2013.000000       4.000000      12.000000  1.000000e+00   
std         0.789143       1.067828       3.278684  7.166071e-01   

          month_cos      end_month  end_month_sin  end_month_cos  \
count  1.640100e+05  164010.000000   1.640100e+05   1.640100e+05   
mean  -8.142379e-02       6.253521   1.477518e-02  -8.657907e-02   
min   -1.000000e+00       1.000000  -1.000000e+00  -1.000000e+00   
25%   -8.660254e-01       4.000000  -8.660254e-01  -8.660254e-01   
50%   -1.836970e-16       6.000000   1.224647e-16  -1.836970e-16   
75%    5.000000e-01       9.000000   8.660254e-01   5.000000e-01   
max    1.000000e+00      12.000000   1.000000e+00   1.000000e+00   
std    6.923067e-01       3.266219   7.192986e-01   6.891308e-01   

       is_month_start   is_month_end        weeknum    weeknum_sin  \
count   164010.000000  164010.000000  164010.000000  164010.000000   
mean         

After scrutinizing the description, I noticed that the weekday column has sometimes values 0 sometimes 1! which is odd, becasue it is expected that all weeks should be starting on the same day (Monday). It might not sound like a big deal if we just drop the weekday feature (it is supposed to always be the same day anyway); BUT, we are extracting all these features such as month, quarter and year, that could be influenced by that 1-day shift and skew our final features and predictions! So we better drill down on where this issue might be rising from:

In [18]:
combined_df[combined_df['weekday']==1].head()

record_ID       week  store_id  sku_id  total_price  base_price  \
68145      96456 2012-03-06      8091  216418     104.0250    104.0250   
68146      96457 2012-03-06      8091  216419     102.6000    102.6000   
68147      96458 2012-03-06      8091  216425     118.9875    134.6625   
68148      96459 2012-03-06      8091  216233     118.2750    133.2375   
68149      96460 2012-03-06      8091  217390     168.8625    168.8625   

       is_featured_sku  is_display_sku  units_sold     diff  \
68145                0               0        30.0   0.0000   
68146                0               0        42.0   0.0000   
68147                0               0        13.0  15.6750   
68148                0               0        19.0  14.9625   
68149                0               0        25.0   0.0000   

       relative_diff_total  relative_diff_base weekend_date  year  end_year  \
68145             0.000000            0.000000   2012-03-12  2012      2012   
68146             0.000000            0.000000   2012-03-12  2012      2012   
68147             0.131737            0.116402   2012-03-12  2012      2012   
68148             0.126506            0.112299   2012-03-12  2012      2012   
68149             0.000000            0.000000   2012-03-12  2012      2012   

       quarter  month  month_sin     month_cos  end_month  end_month_sin  \
68145        1      3        1.0  6.123234e-17          3            1.0   
68146        1      3        1.0  6.123234e-17          3            1.0   
68147        1      3        1.0  6.123234e-17          3            1.0   
68148        1      3        1.0  6.123234e-17          3            1.0   
68149        1      3        1.0  6.123234e-17          3            1.0   

       end_month_cos  is_month_start  is_month_end  weeknum  weeknum_sin  \
68145   6.123234e-17               0             0       10     0.935016   
68146   6.123234e-17               0             0       10     0.935016   
68147   6.123234e-17               0             0       10     0.935016   
68148   6.123234e-17               0             0       10     0.935016   
68149   6.123234e-17               0             0       10     0.935016   

       weeknum_cos  week_from_start  day  weekday  
68145     0.354605               59    6        1  
68146     0.354605               59    6        1  
68147     0.354605               59    6        1  
68148     0.354605               59    6        1  
68149     0.354605               59    6        1

In [19]:
combined_df[combined_df['weekday']==0].tail()

record_ID       week  store_id  sku_id  total_price  base_price  \
68140      96449 2012-02-27      9984  223245     201.6375    201.6375   
68141      96450 2012-02-27      9984  223153     221.5875    221.5875   
68142      96453 2012-02-27      9984  245338     469.5375    469.5375   
68143      96454 2012-02-27      9984  547934     142.5000    173.8500   
68144      96455 2012-02-27      9984  679023     213.0375    213.0375   

       is_featured_sku  is_display_sku  units_sold   diff  \
68140                0               0        45.0   0.00   
68141                0               0        46.0   0.00   
68142                0               0        22.0   0.00   
68143                0               0        11.0  31.35   
68144                0               0         9.0   0.00   

       relative_diff_total  relative_diff_base weekend_date  year  end_year  \
68140                 0.00            0.000000   2012-03-04  2012      2012   
68141                 0.00            0.000000   2012-03-04  2012      2012   
68142                 0.00            0.000000   2012-03-04  2012      2012   
68143                 0.22            0.180328   2012-03-04  2012      2012   
68144                 0.00            0.000000   2012-03-04  2012      2012   

       quarter  month  month_sin  month_cos  end_month  end_month_sin  \
68140        1      2   0.866025        0.5          3            1.0   
68141        1      2   0.866025        0.5          3            1.0   
68142        1      2   0.866025        0.5          3            1.0   
68143        1      2   0.866025        0.5          3            1.0   
68144        1      2   0.866025        0.5          3            1.0   

       end_month_cos  is_month_start  is_month_end  weeknum  weeknum_sin  \
68140   6.123234e-17               0             0        9     0.885456   
68141   6.123234e-17               0             0        9     0.885456   
68142   6.123234e-17               0             0        9     0.885456   
68143   6.123234e-17               0             0        9     0.885456   
68144   6.123234e-17               0             0        9     0.885456   

       weeknum_cos  week_from_start  day  weekday  
68140     0.464723               58   27        0  
68141     0.464723               58   27        0  
68142     0.464723               58   27        0  
68143     0.464723               58   27        0  
68144     0.464723               58   27        0

Interestingly, all weekdays up until (including) 02/27/2012 were Monday (0), and starting 03/06/2012 they are all Tuesday (1). Thinking about this specific date that this is happening, I looked at the calendar and found out that 2012 was a leap year! So before creating our time features, we shift back one day the 'week' column entries on and after 03/06/2012:


In [20]:
def fix_leap_year_shift(df):
    
    problematic_start_date = pd.to_datetime('2012-03-06')
    rows_to_fix_mask = (df['week'] >= problematic_start_date)
    df.loc[rows_to_fix_mask, 'week'] = df.loc[rows_to_fix_mask, 'week'] - pd.Timedelta(days=1)
        
    return df
combined_df = fix_leap_year_shift(combined_df)

Now we can recreate the time features and overwrite the wrong ones we made before:

In [21]:
combined_df['weekend_date'] = combined_df['week'] + pd.to_timedelta(6, unit='D')
combined_df = extract_time_features(combined_df)
combined_df[combined_df['weekday']==1]['weekday'].count()

0

<span style="color:#003366; background-color:#F0F8FF; font-size: 26px; font-weight: bold; font-style: italic;"> Holiday Feature  </span>

Since holidays could impact the demand for certain SKU's, it is prudent to create a binary is_holiday feature, 1 if there is a holiday in the week, 0 if not:

In [22]:
years_in_data = combined_df['week'].dt.year.unique()
us_holidays = holidays.US(years=years_in_data)
holiday_dates = set(us_holidays.keys())

# Create a set of all possible week-start dates that contain a holiday
# For each holiday, any week starting up to 6 days before it will include it.
holiday_week_starts = set()
for h_date in holiday_dates:
    for i in range(7):
        possible_start_date = h_date - timedelta(days=i)
        holiday_week_starts.add(possible_start_date)

combined_df['is_holiday'] = combined_df['week'].dt.date.isin(holiday_week_starts).astype(int)
combined_df[combined_df['is_holiday']==1].head()

record_ID       week  store_id  sku_id  total_price  base_price  \
0          1 2011-01-17      8091  216418      99.0375    111.8625   
1          2 2011-01-17      8091  216419      99.0375     99.0375   
2          3 2011-01-17      8091  216425     133.9500    133.9500   
3          4 2011-01-17      8091  216233     133.9500    133.9500   
4          5 2011-01-17      8091  217390     141.0750    141.0750   

   is_featured_sku  is_display_sku  units_sold    diff  relative_diff_total  \
0                0               0        20.0  12.825             0.129496   
1                0               0        28.0   0.000             0.000000   
2                0               0        19.0   0.000             0.000000   
3                0               0        44.0   0.000             0.000000   
4                0               0        52.0   0.000             0.000000   

   relative_diff_base weekend_date  year  end_year  quarter  month  month_sin  \
0             0.11465   2011-01-23  2011      2011        1      1        0.5   
1             0.00000   2011-01-23  2011      2011        1      1        0.5   
2             0.00000   2011-01-23  2011      2011        1      1        0.5   
3             0.00000   2011-01-23  2011      2011        1      1        0.5   
4             0.00000   2011-01-23  2011      2011        1      1        0.5   

   month_cos  end_month  end_month_sin  end_month_cos  is_month_start  \
0   0.866025          1            0.5       0.866025               0   
1   0.866025          1            0.5       0.866025               0   
2   0.866025          1            0.5       0.866025               0   
3   0.866025          1            0.5       0.866025               0   
4   0.866025          1            0.5       0.866025               0   

   is_month_end  weeknum  weeknum_sin  weeknum_cos  week_from_start  day  \
0             0        3     0.354605     0.935016                0   17   
1             0        3     0.354605     0.935016                0   17   
2             0        3     0.354605     0.935016                0   17   
3             0        3     0.354605     0.935016                0   17   
4             0        3     0.354605     0.935016                0   17   

   weekday  is_holiday  
0        0           1  
1        0           1  
2        0           1  
3        0           1  
4        0           1

<span style="color:#003366; background-color:#F0F8FF; font-size: 26px; font-weight: bold; font-style: italic;"> Lag and Moving Average Features  </span>

Since we can only — for now — get the train dataframe lag and MA features, as we have yet no prediction values, we need to get our train dataframe back from the combined_df:

In [23]:
train = combined_df[:len(train)].copy()

In [24]:
test = combined_df[len(train):].copy()
test['units_sold']= -1
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13860 entries, 150150 to 164009
Data columns (total 31 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   record_ID            13860 non-null  int64         
 1   week                 13860 non-null  datetime64[ns]
 2   store_id             13860 non-null  int64         
 3   sku_id               13860 non-null  int64         
 4   total_price          13860 non-null  float64       
 5   base_price           13860 non-null  float64       
 6   is_featured_sku      13860 non-null  int64         
 7   is_display_sku       13860 non-null  int64         
 8   units_sold           13860 non-null  int64         
 9   diff                 13860 non-null  float64       
 10  relative_diff_total  13860 non-null  float64       
 11  relative_diff_base   13860 non-null  float64       
 12  weekend_date         13860 non-null  datetime64[ns]
 13  year                 1386

In order to extract some lagged and moving average features, I plot the weekly demand, ACF and PACF plots for all SKU's. A general rule of thumb says that lags up to N/3 should be considered for lag and moving average features (where N is number of data points in the time series) so we first calculate that
  

In [25]:
nlags = train['week_from_start'].nunique()/3
nlags

43.333333333333336

Since it is pretty close to a year cycle of 52 weeks, we will be generous and consider up to 55 lags (sometimes certain holidays like Easter can happen again after 55 weeks at most): 

In [26]:
nlags = 55
sku_weekly_demand = train.groupby(['sku_id', 'week'])['units_sold'].sum().reset_index()
unique_skus = sku_weekly_demand['sku_id'].unique()

# Create a figure with 3 vertically stacked subplots
fig = make_subplots(
    rows=3, cols=1,
    subplot_titles=("Time Series", "Autocorrelation (ACF)", "Partial Autocorrelation (PACF)")
)

for sku in unique_skus:
   
    sku_data = sku_weekly_demand[sku_weekly_demand['sku_id'] == sku]

    fig.add_trace(go.Scatter(
        x=sku_data['week'], y=sku_data['units_sold'], name='Sales'
    ), row=1, col=1)

    acf_vals, acf_confint = acf(sku_data['units_sold'], alpha=0.05, nlags=nlags)
    lags = np.arange(len(acf_vals))
    
    fig.add_trace(go.Bar(
        x=lags, y=acf_vals, name='ACF'
    ), row=2, col=1)
    # Add ACF confidence intervals
    fig.add_trace(go.Scatter(
        x=lags, y=acf_confint[:, 0] - acf_vals, line=dict(width=0), showlegend=False
    ), row=2, col=1)
    fig.add_trace(go.Scatter(
        x=lags, y=acf_confint[:, 1] - acf_vals, line=dict(width=0), fill='tonexty',
        fillcolor='rgba(0,100,80,0.2)', showlegend=False
    ), row=2, col=1)

    pacf_vals, pacf_confint = pacf(sku_data['units_sold'], alpha=0.05, nlags=nlags)
    lags_pacf = np.arange(len(pacf_vals))

    fig.add_trace(go.Bar(
        x=lags_pacf, y=pacf_vals, name='PACF'
    ), row=3, col=1)
    # Add PACF confidence intervals
    fig.add_trace(go.Scatter(
        x=lags_pacf, y=pacf_confint[:, 0] - pacf_vals, line=dict(width=0), showlegend=False
    ), row=3, col=1)
    fig.add_trace(go.Scatter(
        x=lags_pacf, y=pacf_confint[:, 1] - pacf_vals, line=dict(width=0), fill='tonexty',
        fillcolor='rgba(0,100,80,0.2)', showlegend=False
    ), row=3, col=1)


# Create the dropdown menu
buttons = []
# Each SKU corresponds to 7 traces (1 for time series, 3 for ACF, 3 for PACF)
traces_per_sku = 7 
for i, sku in enumerate(unique_skus):
    visibility = [False] * (len(unique_skus) * traces_per_sku)
    for j in range(traces_per_sku):
        visibility[i * traces_per_sku + j] = True

    button = dict(
        label=f"SKU: {sku}",
        method='update',
        args=[{'visible': visibility}]
    )
    buttons.append(button)

fig.update_layout(
    updatemenus=[dict(
        active=0,
        buttons=buttons,
        direction="down",
        pad={"r": 10, "t": 10},
        showactive=True,
        x=0.1,
        xanchor="left",
        y=1.15,
        yanchor="top"
    )],
    title_text="Sales and Autocorrelation Analysis by SKU",
    title_x=0.5,
    height=800 
)
fig.update_xaxes(title_text="Lag", row=2, col=1)
fig.update_xaxes(title_text="Lag", row=3, col=1)
# Make the traces for the first SKU visible by default
for i in range(traces_per_sku, len(fig.data)):
    fig.data[i].visible = False

fig.show()

based on these PACF plots I determined the best lag features for each SKU; and based on the ACF plots I determined the best moving average features for each SKU as below:

In [27]:
sku_specific_lags = {
    216233: ['lag_1_weeks', 'lag_11_weeks', 'lag_25_weeks', 'lag_36_weeks', 'lag_44_weeks', 'lag_51_weeks', 'lag_52_weeks', 
             'lag_53_weeks', 'lag_55_weeks'],
    216418: ['lag_1_weeks', 'lag_2_weeks', 'lag_5_weeks', 'lag_19_weeks', 'lag_34_weeks', 'lag_37_weeks', 'lag_51_weeks',
            'lag_54_weeks'], 
    216419: ['lag_1_weeks', 'lag_2_weeks','lag_37_weeks', 'lag_40_weeks', 'lag_43_weeks', 'lag_49_weeks', 'lag_55_weeks'],
    216425: ['lag_1_weeks', 'lag_8_weeks', 'lag_35_weeks', 'lag_43_weeks', 'lag_49_weeks'],  
    217217: ['lag_1_weeks','lag_10_weeks', 'lag_25_weeks','lag_36_weeks','lag_39_weeks','lag_41_weeks','lag_54_weeks'],
    217390: ['lag_1_weeks', 'lag_33_weeks', 'lag_42_weeks', 'lag_43_weeks', 'lag_44_weeks', 'lag_47_weeks'],
    217777: ['lag_1_weeks','lag_3_weeks','lag_4_weeks', 'lag_10_weeks','lag_26_weeks','lag_50_weeks', 'lag_54_weeks'],
    219009: ['lag_1_weeks', 'lag_3_weeks', 'lag_34_weeks'],
    219029: ['lag_1_weeks', 'lag_2_weeks', 'lag_5_weeks', 'lag_25_weeks','lag_33_weeks', 'lag_38_weeks', 'lag_39_weeks', 
             'lag_48_weeks','lag_49_weeks', 'lag_50_weeks', 'lag_52_weeks'], 
    219844: ['lag_1_weeks', 'lag_10_weeks', 'lag_36_weeks', 'lag_54_weeks'],
    222087: ['lag_11_weeks', 'lag_24_weeks', 'lag_33_weeks', 'lag_54_weeks', 'lag_55_weeks'],
    222765: ['lag_1_weeks', 'lag_40_weeks', 'lag_43_weeks', 'lag_53_weeks'], 
    223153: ['lag_1_weeks', 'lag_17_weeks', 'lag_34_weeks', 'lag_50_weeks', 'lag_52_weeks', 'lag_54_weeks'],
    223245: ['lag_1_weeks', 'lag_13_weeks', 'lag_24_weeks', 'lag_54_weeks'],
    245338: ['lag_1_weeks', 'lag_19_weeks', 'lag_24_weeks', 'lag_37_weeks', 'lag_43_weeks', 'lag_48_weeks',
             'lag_51_weeks', 'lag_52_weeks', 'lag_53_weeks'],
    245387: ['lag_1_weeks', 'lag_19_weeks', 'lag_24_weeks', 'lag_37_weeks', 'lag_43_weeks', 'lag_44_weeks', 'lag_51_weeks',
             'lag_52_weeks', 'lag_53_weeks'],
    300021: ['lag_1_weeks', 'lag_2_weeks', 'lag_42_weeks', 'lag_54_weeks'],
    300291: ['lag_1_weeks','lag_4_weeks', 'lag_19_weeks','lag_36_weeks', 'lag_50_weeks','lag_53_weeks', 'lag_54_weeks'], 
    320485: ['lag_1_weeks', 'lag_3_weeks', 'lag_20_weeks', 'lag_23_weeks', 'lag_42_weeks', 'lag_47_weeks', 'lag_53_weeks'],
    327492: ['lag_1_weeks','lag_12_weeks', 'lag_28_weeks','lag_34_weeks', 'lag_52_weeks', 'lag_53_weeks'],
    378934: ['lag_1_weeks', 'lag_2_weeks', 'lag_9_weeks', 'lag_22_weeks',  'lag_23_weeks', 'lag_35_weeks', 'lag_42_weeks',
             'lag_53_weeks'],
    398721: ['lag_1_weeks', 'lag_19_weeks', 'lag_24_weeks', 'lag_28_weeks', 'lag_37_weeks', 'lag_43_weeks', 
            'lag_48_weeks', 'lag_49_weeks', 'lag_51_weeks', 'lag_53_weeks'],
    545621: ['lag_1_weeks', 'lag_35_weeks', 'lag_47_weeks', 'lag_51_weeks', 'lag_54_weeks'],
    546789: ['lag_1_weeks','lag_2_weeks', 'lag_23_weeks','lag_25_weeks', 'lag_52_weeks','lag_54_weeks'],
    547934: ['lag_1_weeks'],
    600934: ['lag_1_weeks','lag_2_weeks', 'lag_41_weeks','lag_42_weeks', 'lag_44_weeks','lag_53_weeks'], 
    673209: ['lag_1_weeks', 'lag_28_weeks','lag_39_weeks', 'lag_53_weeks'], 
    679023: ['lag_1_weeks','lag_2_weeks', 'lag_40_weeks','lag_43_weeks']
}

In [28]:
sku_specific_moving_averages = {
    216233: ['MA_1_weeks', 'MA_2_weeks'],
    216418: ['MA_1_weeks', 'MA_2_weeks', 'MA_3_weeks', 'MA_4_weeks', 'MA_5_weeks'], 
    216419: ['MA_1_weeks', 'MA_2_weeks','MA_3_weeks', 'MA_4_weeks', 'MA_5_weeks'],
    216425: ['MA_1_weeks', 'MA_2_weeks'], 
    217217: ['MA_1_weeks', 'MA_2_weeks', 'MA_3_weeks'],
    217390: ['MA_1_weeks'],
    217777: ['MA_1_weeks', 'MA_2_weeks', 'MA_3_weeks'],
    219009: ['MA_1_weeks', 'MA_2_weeks'],
    219029: ['MA_1_weeks'], 
    219844: ['MA_1_weeks', 'MA_2_weeks', 'MA_3_weeks'],
    222087: [],
    222765: ['MA_1_weeks'],
    223153: ['MA_1_weeks'],
    223245: ['MA_1_weeks'],
    245338: ['MA_1_weeks'],
    245387: ['MA_1_weeks'],
    300021: ['MA_1_weeks', 'MA_2_weeks', 'MA_3_weeks', 'MA_4_weeks', 'MA_5_weeks', 'MA_6_weeks'], 
    300291: ['MA_1_weeks'],
    320485: ['MA_1_weeks', 'MA_2_weeks'],
    327492: ['MA_1_weeks', 'MA_2_weeks'],
    378934: ['MA_1_weeks', 'MA_2_weeks'],
    398721: ['MA_1_weeks'],
    545621: ['MA_1_weeks'],
    546789: ['MA_1_weeks'],
    547934: ['MA_1_weeks'],
    600934: ['MA_1_weeks'], 
    673209: ['MA_1_weeks', 'MA_2_weeks'], 
    679023: ['MA_1_weeks']
}

The following two functions make the lag and moving average features for our train data set:

In [29]:
def create_lag_features(df, lags, history=None):
    
    df_copy = df.copy()
 
    if history is not None:
        source_data = pd.concat([history, df_copy], ignore_index=True)
    else:
        source_data = df_copy

    sku_weekly_sales = source_data.groupby(['sku_id', 'week'])['units_sold'].sum().reset_index()
    sku_weekly_sales = sku_weekly_sales.sort_values(by=['sku_id', 'week'])

    for lag in lags:
        feature_name = f'lag_{lag}_weeks'
        sku_weekly_sales[feature_name] = sku_weekly_sales.groupby('sku_id')['units_sold'].shift(lag)
 
    new_feature_cols = [f'lag_{lag}_weeks' for lag in lags]
    cols_to_merge = ['sku_id', 'week'] + new_feature_cols
    
    df_copy_clean = df_copy.drop(columns=new_feature_cols, errors='ignore')

    df_with_lags = pd.merge(
        df_copy_clean,
        sku_weekly_sales[cols_to_merge],
        on=['sku_id', 'week'],
        how='left'
    )

    df_with_lags[new_feature_cols] = df_with_lags[new_feature_cols].fillna(0)
    
    return df_with_lags

In [30]:
def create_moving_average_features(df, window_sizes, history=None):
   
    df_copy = df.copy()
    
    source_data = pd.concat([history, df_copy], ignore_index=True) if history is not None else df_copy
    
    sku_weekly_sales = source_data.groupby(['sku_id', 'week'])['units_sold'].sum().reset_index()
    sku_weekly_sales = sku_weekly_sales.sort_values(by=['sku_id', 'week'])
 
    for window in window_sizes:
        feature_name = f'MA_{window}_weeks'
        sku_weekly_sales[feature_name] = sku_weekly_sales.groupby('sku_id')['units_sold'].transform(
            lambda x: x.shift(1).rolling(window=window, min_periods=1).mean()
        )

    new_feature_cols = [f'MA_{window}_weeks' for window in window_sizes]
    cols_to_merge = ['sku_id', 'week'] + new_feature_cols

    df_copy_clean = df_copy.drop(columns=new_feature_cols, errors='ignore')

    df_with_features = pd.merge(
        df_copy_clean,
        sku_weekly_sales[cols_to_merge],
        on=['sku_id', 'week'],
        how='left'
    )

    df_with_features[new_feature_cols] = df_with_features[new_feature_cols].fillna(0)
    
    return df_with_features

In [31]:
lags = [1, 2, 3, 4, 5, 8, 9, 10, 11, 12, 13, 17, 19, 20, 22, 23,
         24, 25, 26, 28, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42,
         43, 44, 47, 48, 49, 50, 51, 52, 53, 54, 55]
window_sizes = [1,2,3,4,5,6]
train = create_lag_features(train, lags)
train = create_moving_average_features(train, window_sizes)

*Nota Bene:* These two functions will also be used later in recursive forecasting loop, in which stage, the history arg of the functions will be used.

In [32]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 150150 entries, 0 to 150149
Data columns (total 78 columns):
 #   Column               Non-Null Count   Dtype         
---  ------               --------------   -----         
 0   record_ID            150150 non-null  int64         
 1   week                 150150 non-null  datetime64[ns]
 2   store_id             150150 non-null  int64         
 3   sku_id               150150 non-null  int64         
 4   total_price          150150 non-null  float64       
 5   base_price           150150 non-null  float64       
 6   is_featured_sku      150150 non-null  int64         
 7   is_display_sku       150150 non-null  int64         
 8   units_sold           150150 non-null  float64       
 9   diff                 150150 non-null  float64       
 10  relative_diff_total  150150 non-null  float64       
 11  relative_diff_base   150150 non-null  float64       
 12  weekend_date         150150 non-null  datetime64[ns]
 13  year          

<span style="color:#003366; background-color:#F0F8FF; font-size: 26px; font-weight: bold; font-style: italic;"> Store Trend Features  </span>

we have so far fully discussed the lag and moving average features of each SKU, but what about stores? A store might have been consistently increasing or decreasing its sales! Foregoing such analysis would be detrimental to the results! 

In [33]:
nlags = 55
store_weekly_demand = train.groupby(['store_id', 'week'])['units_sold'].sum().reset_index()
unique_stores = store_weekly_demand['store_id'].unique()

fig = make_subplots(
    rows=3, cols=1,
    subplot_titles=("Time Series", "Autocorrelation (ACF)", "Partial Autocorrelation (PACF)")
)

for store in unique_stores:

    store_data = store_weekly_demand[store_weekly_demand['store_id'] == store]

    fig.add_trace(go.Scatter(
        x=store_data['week'], y=store_data['units_sold'], name='Sales'
    ), row=1, col=1)

    acf_vals, acf_confint = acf(store_data['units_sold'], alpha=0.05, nlags=nlags)
    lags = np.arange(len(acf_vals))

    fig.add_trace(go.Bar(
        x=lags, y=acf_vals, name='ACF'
    ), row=2, col=1)

    fig.add_trace(go.Scatter(
        x=lags, y=acf_confint[:, 0] - acf_vals, line=dict(width=0), showlegend=False
    ), row=2, col=1)
    fig.add_trace(go.Scatter(
        x=lags, y=acf_confint[:, 1] - acf_vals, line=dict(width=0), fill='tonexty',
        fillcolor='rgba(0,100,80,0.2)', showlegend=False
    ), row=2, col=1)

    pacf_vals, pacf_confint = pacf(store_data['units_sold'], alpha=0.05, nlags=nlags)
    lags_pacf = np.arange(len(pacf_vals))

    fig.add_trace(go.Bar(
        x=lags_pacf, y=pacf_vals, name='PACF'
    ), row=3, col=1)

    fig.add_trace(go.Scatter(
        x=lags_pacf, y=pacf_confint[:, 0] - pacf_vals, line=dict(width=0), showlegend=False
    ), row=3, col=1)
    fig.add_trace(go.Scatter(
        x=lags_pacf, y=pacf_confint[:, 1] - pacf_vals, line=dict(width=0), fill='tonexty',
        fillcolor='rgba(0,100,80,0.2)', showlegend=False
    ), row=3, col=1)

buttons = []

traces_per_store = 7 
for i, store in enumerate(unique_stores):
  
    visibility = [False] * (len(unique_stores) * traces_per_store)
    for j in range(traces_per_store):
        visibility[i * traces_per_store + j] = True

    button = dict(
        label=f"store: {store}",
        method='update',
        args=[{'visible': visibility}]
    )
    buttons.append(button)

fig.update_layout(
    updatemenus=[dict(
        active=0,
        buttons=buttons,
        direction="down",
        pad={"r": 10, "t": 10},
        showactive=True,
        x=0.1,
        xanchor="left",
        y=1.15,
        yanchor="top"
    )],
    title_text="Sales and Autocorrelation Analysis by store",
    title_x=0.5,
    height=800 
)
fig.update_xaxes(title_text="Lag", row=2, col=1)
fig.update_xaxes(title_text="Lag", row=3, col=1)

for i in range(traces_per_store, len(fig.data)):
    fig.data[i].visible = False

fig.show()

There are not a lot of stores with large PACF peaks or visible trends, so for simplicity, I consider a general linear-regression trend and a 26-week moving average feature for each store:

In [34]:
def create_store_trend_feature(df):

    if 'week_from_start' not in df.columns:
        print("Warning: 'week_from_start' column not found. Creating a default one.")
        df['week_from_start'] = (df['week'] - df['week'].min()).dt.days // 7

    store_weekly_demand = df.groupby(['store_id', 'week', 'week_from_start'])['units_sold'].sum().reset_index()

    all_trends = []

    for store_id in store_weekly_demand['store_id'].unique():
        store_data = store_weekly_demand[store_weekly_demand['store_id'] == store_id].copy()
        
        X = store_data[['week_from_start']]
        y = store_data['units_sold']
        
        model = LinearRegression()
        model.fit(X, y)
        
        store_data['store_trend'] = model.predict(X)
        all_trends.append(store_data)
        
    trend_df = pd.concat(all_trends)

    df = pd.merge(
        df,
        trend_df[['store_id', 'week', 'store_trend']],
        on=['store_id', 'week'],
        how='left'
    )
   
    return df

In [35]:
def create_moving_average_features_store(df, windows, history=None):
 
    df_copy = df.copy()

    source_data = pd.concat([history, df_copy], ignore_index=True) if history is not None else df_copy
    source_data['week'] = pd.to_datetime(source_data['week'])

    store_weekly_sales = source_data.groupby(['store_id', 'week'])['units_sold'].sum().reset_index()
    store_weekly_sales = store_weekly_sales.sort_values(by=['store_id', 'week'])

    for window in windows:
        feature_name = f'store_moving_avg_{window}_weeks'
        store_weekly_sales[feature_name] = store_weekly_sales.groupby('store_id')['units_sold'].transform(
            lambda x: x.shift(1).rolling(window=window, min_periods=1).mean()
        )

    new_feature_cols = [f'store_moving_avg_{w}_weeks' for w in windows]
    cols_to_merge = ['store_id', 'week'] + new_feature_cols
    
    # Preserve original index for correct ordering
    df_copy = df_copy.reset_index()

    df_copy_clean = df_copy.drop(columns=new_feature_cols, errors='ignore')
    
    df_with_features = pd.merge(
        df_copy_clean,
        store_weekly_sales[cols_to_merge],
        on=['store_id', 'week'],
        how='left'
    )

    df_with_features[new_feature_cols] = df_with_features[new_feature_cols].fillna(0)
    
    return df_with_features.set_index('index').sort_index()

In [36]:
# gotta make combined_df again to get the trend of store extrapolated for the test dataframe weeks as well:
combined_df = pd.concat([train, test], ignore_index=True)
combined_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 164010 entries, 0 to 164009
Data columns (total 78 columns):
 #   Column               Non-Null Count   Dtype         
---  ------               --------------   -----         
 0   record_ID            164010 non-null  int64         
 1   week                 164010 non-null  datetime64[ns]
 2   store_id             164010 non-null  int64         
 3   sku_id               164010 non-null  int64         
 4   total_price          164010 non-null  float64       
 5   base_price           164010 non-null  float64       
 6   is_featured_sku      164010 non-null  int64         
 7   is_display_sku       164010 non-null  int64         
 8   units_sold           164010 non-null  float64       
 9   diff                 164010 non-null  float64       
 10  relative_diff_total  164010 non-null  float64       
 11  relative_diff_base   164010 non-null  float64       
 12  weekend_date         164010 non-null  datetime64[ns]
 13  year          

In [37]:
combined_df = create_store_trend_feature(combined_df)
combined_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 164010 entries, 0 to 164009
Data columns (total 79 columns):
 #   Column               Non-Null Count   Dtype         
---  ------               --------------   -----         
 0   record_ID            164010 non-null  int64         
 1   week                 164010 non-null  datetime64[ns]
 2   store_id             164010 non-null  int64         
 3   sku_id               164010 non-null  int64         
 4   total_price          164010 non-null  float64       
 5   base_price           164010 non-null  float64       
 6   is_featured_sku      164010 non-null  int64         
 7   is_display_sku       164010 non-null  int64         
 8   units_sold           164010 non-null  float64       
 9   diff                 164010 non-null  float64       
 10  relative_diff_total  164010 non-null  float64       
 11  relative_diff_base   164010 non-null  float64       
 12  weekend_date         164010 non-null  datetime64[ns]
 13  year          

In [38]:
# Now gotta take the train out of combined to make the store MA feature, 
# cant yet make that feature for test df coz have no predicitons yet; we will do that in recursive forecasting loop later
train = combined_df[:len(train)].copy()
test = combined_df[len(train):].copy()

train = create_moving_average_features_store(train, windows=[26])
train.info()

<class 'pandas.core.frame.DataFrame'>
Index: 150150 entries, 0 to 150149
Data columns (total 80 columns):
 #   Column                     Non-Null Count   Dtype         
---  ------                     --------------   -----         
 0   record_ID                  150150 non-null  int64         
 1   week                       150150 non-null  datetime64[ns]
 2   store_id                   150150 non-null  int64         
 3   sku_id                     150150 non-null  int64         
 4   total_price                150150 non-null  float64       
 5   base_price                 150150 non-null  float64       
 6   is_featured_sku            150150 non-null  int64         
 7   is_display_sku             150150 non-null  int64         
 8   units_sold                 150150 non-null  float64       
 9   diff                       150150 non-null  float64       
 10  relative_diff_total        150150 non-null  float64       
 11  relative_diff_base         150150 non-null  float64      

In [39]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13860 entries, 150150 to 164009
Data columns (total 79 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   record_ID            13860 non-null  int64         
 1   week                 13860 non-null  datetime64[ns]
 2   store_id             13860 non-null  int64         
 3   sku_id               13860 non-null  int64         
 4   total_price          13860 non-null  float64       
 5   base_price           13860 non-null  float64       
 6   is_featured_sku      13860 non-null  int64         
 7   is_display_sku       13860 non-null  int64         
 8   units_sold           13860 non-null  float64       
 9   diff                 13860 non-null  float64       
 10  relative_diff_total  13860 non-null  float64       
 11  relative_diff_base   13860 non-null  float64       
 12  weekend_date         13860 non-null  datetime64[ns]
 13  year                 1386

# <span style="color: purple; background-color: None; font-size: 36px; font-weight: bold; font-style: italic;"> Feature Impact Assessment </span>

As I select features I gauge if the validation error improves. In case of improvement I use the feature; otherwise, I disard it. for this purpose, I define an error function:

In [40]:
def RMSLE (actual, predicted):
    predcited = np.array ([np.log(np.abs(x+1)) for x in predicted])
    actual = np.array ([np.log(np.abs(x+1)) for x in actual])
    log_error = predicted - actual
    return 100*np.sqrt(np.mean(log_error**2))

In [41]:
cols = [
    'base_price', 'total_price', 'diff', 'relative_diff_base', 'relative_diff_total',
    'is_featured_sku', 'is_display_sku',
]

store_encoder = MEstimateEncoder(cols=['store_id'])
store_encoder.fit(train[['store_id']], train['units_sold'])
train['store_encoded'] = store_encoder.transform(train[['store_id']])
test['store_encoded'] = store_encoder.transform(test[['store_id']])

cols += ['store_encoded']
# here RMSLE was 4750
cols += ['year','end_year', 'quarter', 'month_sin', 'month_cos', 'end_month_sin', 'end_month_cos',
         'is_month_start', 'is_month_end', 'weeknum_sin', 'weeknum_cos', 'week_from_start','day','is_holiday'] 
# here 4573

error = 0
skus = train['sku_id'].unique()
for sku_id in skus:
    
    train_sku = train[train['sku_id'] == sku_id].copy().sort_values('week')

    X_sku = train_sku[cols]
    y_sku = np.log1p(train_sku['units_sold'])

    Xtrain, Xval, ytrain, yval = train_test_split (X_sku, y_sku, test_size = 0.2, random_state = random_seed)

    reg = RandomForestRegressor()
    reg.fit(Xtrain, ytrain)
    
    predVal = reg.predict(Xval)
    
    print(f'Baseline Regression RMSLE for sku_id {sku_id}: {RMSLE(np.expm1(yval), np.expm1(predVal))}')
    error += RMSLE(np.expm1(yval), np.expm1(predVal))

error /= train['sku_id'].nunique()
print(f'Average validation RMSLE: {error}')

Baseline Regression RMSLE for sku_id 216418: 10246.24988054365
Baseline Regression RMSLE for sku_id 216419: 7986.14182187952
Baseline Regression RMSLE for sku_id 216425: 3557.3908235363765
Baseline Regression RMSLE for sku_id 216233: 4671.599151057439
Baseline Regression RMSLE for sku_id 217390: 7332.680778802687
Baseline Regression RMSLE for sku_id 219009: 13414.387335006004
Baseline Regression RMSLE for sku_id 219029: 6991.594442267109
Baseline Regression RMSLE for sku_id 223245: 9179.017401372563
Baseline Regression RMSLE for sku_id 223153: 8741.731392444124
Baseline Regression RMSLE for sku_id 300021: 4726.636124319689
Baseline Regression RMSLE for sku_id 219844: 2816.38550002226
Baseline Regression RMSLE for sku_id 222087: 7666.486929100384
Baseline Regression RMSLE for sku_id 320485: 3016.424745059291
Baseline Regression RMSLE for sku_id 378934: 2381.7819512556116
Baseline Regression RMSLE for sku_id 222765: 5943.625786897367
Baseline Regression RMSLE for sku_id 245387: 3093.5858

It's very important to keep this number **4750** in mind as our baseline error: if by adding a feature it decreases, it means that's a good feature; otherwise, the feature should not be employed. So, let's explore all the other features we created one by one:

Adding basic time features improved the RMSLE to 4573, now let's add the lag features for each SKU:

In [42]:
cols = [
    'base_price', 'total_price', 'diff', 'relative_diff_base', 'relative_diff_total',
    'is_featured_sku', 'is_display_sku',
]

store_encoder = MEstimateEncoder(cols=['store_id'])
store_encoder.fit(train[['store_id']], train['units_sold'])
train['store_encoded'] = store_encoder.transform(train[['store_id']])
test['store_encoded'] = store_encoder.transform(test[['store_id']])

cols += ['store_encoded']

cols += ['year','end_year', 'quarter', 'month_sin', 'month_cos', 'end_month_sin', 'end_month_cos',
         'is_month_start', 'is_month_end', 'weeknum_sin', 'weeknum_cos', 'week_from_start','day','is_holiday'] 


final_feature_sets = {}
for sku_id, custom_lags in sku_specific_lags.items():
    final_feature_sets[sku_id] = cols + custom_lags


error = 0
skus = train['sku_id'].unique()
for sku_id, cols in final_feature_sets.items():
    
    train_sku = train[train['sku_id'] == sku_id].copy().sort_values('week')

    X_sku = train_sku[cols]
    y_sku = np.log1p(train_sku['units_sold'])

    Xtrain, Xval, ytrain, yval = train_test_split (X_sku, y_sku, test_size = 0.2, random_state = random_seed)

    reg = RandomForestRegressor()
    reg.fit(Xtrain, ytrain)
    
    predVal = reg.predict(Xval)
    
    print(f'Baseline Regression RMSLE for sku_id {sku_id}: {RMSLE(np.expm1(yval), np.expm1(predVal))}')
    error += RMSLE(np.expm1(yval), np.expm1(predVal))

error /= train['sku_id'].nunique()
print(f'Average validation RMSLE: {error}')

Baseline Regression RMSLE for sku_id 216233: 4679.061215457103
Baseline Regression RMSLE for sku_id 216418: 10093.190086107095
Baseline Regression RMSLE for sku_id 216419: 7986.317115770481
Baseline Regression RMSLE for sku_id 216425: 3547.86980272754
Baseline Regression RMSLE for sku_id 217217: 2175.7179087038703
Baseline Regression RMSLE for sku_id 217390: 7310.11233438569
Baseline Regression RMSLE for sku_id 217777: 2243.388791333952
Baseline Regression RMSLE for sku_id 219009: 13577.877485176654
Baseline Regression RMSLE for sku_id 219029: 6987.422070146259
Baseline Regression RMSLE for sku_id 219844: 2778.4139736820202
Baseline Regression RMSLE for sku_id 222087: 7675.219185178142
Baseline Regression RMSLE for sku_id 222765: 5940.774619136266
Baseline Regression RMSLE for sku_id 223153: 8743.616816173571
Baseline Regression RMSLE for sku_id 223245: 9110.794505831605
Baseline Regression RMSLE for sku_id 245338: 4084.535472985145
Baseline Regression RMSLE for sku_id 245387: 3110.492

Great! with all the lag features we got to **4562**, which is an improvement. Let's try adding the moving average features:

In [43]:
for sku_id, custom_MAs in sku_specific_moving_averages.items():
    final_feature_sets[sku_id] = cols + custom_MAs

error = 0
for sku_id, cols in final_feature_sets.items():
    
    train_sku = train[train['sku_id'] == sku_id].copy().sort_values('week')

    X_sku = train_sku[cols]
    y_sku = np.log1p(train_sku['units_sold'])

    Xtrain, Xval, ytrain, yval = train_test_split (X_sku, y_sku, test_size = 0.2, random_state = random_seed)

    reg = RandomForestRegressor()
    reg.fit(Xtrain, ytrain)
    
    predVal = reg.predict(Xval)
    
    print(f'Baseline Regression RMSLE for sku_id {sku_id}: {RMSLE(np.expm1(yval), np.expm1(predVal))}')
    error += RMSLE(np.expm1(yval), np.expm1(predVal))

error /= train['sku_id'].nunique()
print(f'Average validation RMSLE: {error}')

Baseline Regression RMSLE for sku_id 216233: 4682.375357679281
Baseline Regression RMSLE for sku_id 216418: 10130.527453758445
Baseline Regression RMSLE for sku_id 216419: 7972.197427267048
Baseline Regression RMSLE for sku_id 216425: 3542.9316081611732
Baseline Regression RMSLE for sku_id 217217: 2155.1678605380857
Baseline Regression RMSLE for sku_id 217390: 7298.510819580913
Baseline Regression RMSLE for sku_id 217777: 2251.0529478421804
Baseline Regression RMSLE for sku_id 219009: 13563.774082261038
Baseline Regression RMSLE for sku_id 219029: 7079.498144381442
Baseline Regression RMSLE for sku_id 219844: 2775.538198446586
Baseline Regression RMSLE for sku_id 222087: 7671.827530244935
Baseline Regression RMSLE for sku_id 222765: 5943.358234971971
Baseline Regression RMSLE for sku_id 223153: 8741.499198800797
Baseline Regression RMSLE for sku_id 223245: 9203.091510709637
Baseline Regression RMSLE for sku_id 245338: 4096.591931903339
Baseline Regression RMSLE for sku_id 245387: 3105.

RMSLE didn't increase that much, and since these features are meaningful features, we can't just discard them. Probably the final fine-tuned champion model will be able to use such features. Let's try adding store features too:

In [44]:
for sku_id in sku_specific_moving_averages.keys():
    final_feature_sets[sku_id] = cols + ['store_trend','store_moving_avg_26_weeks']
    
error = 0
for sku_id, cols in final_feature_sets.items():
    
    train_sku = train[train['sku_id'] == sku_id].copy().sort_values('week')

    X_sku = train_sku[cols]
    y_sku = np.log1p(train_sku['units_sold'])

    Xtrain, Xval, ytrain, yval = train_test_split (X_sku, y_sku, test_size = 0.2, random_state = random_seed)

    reg = RandomForestRegressor()
    reg.fit(Xtrain, ytrain)
    
    predVal = reg.predict(Xval)
    
    print(f'Baseline Regression RMSLE for sku_id {sku_id}: {RMSLE(np.expm1(yval), np.expm1(predVal))}')
    error += RMSLE(np.expm1(yval), np.expm1(predVal))

error /= train['sku_id'].nunique()
print(f'Average validation RMSLE: {error}')

Baseline Regression RMSLE for sku_id 216233: 4693.048691166255
Baseline Regression RMSLE for sku_id 216418: 10084.99138453395
Baseline Regression RMSLE for sku_id 216419: 7961.543935738172
Baseline Regression RMSLE for sku_id 216425: 3536.1308400251773
Baseline Regression RMSLE for sku_id 217217: 2135.19863109469
Baseline Regression RMSLE for sku_id 217390: 7274.37924900363
Baseline Regression RMSLE for sku_id 217777: 2282.734930479207
Baseline Regression RMSLE for sku_id 219009: 14039.879546520639
Baseline Regression RMSLE for sku_id 219029: 7131.701462031313
Baseline Regression RMSLE for sku_id 219844: 2774.2174732004764
Baseline Regression RMSLE for sku_id 222087: 7642.497742820044
Baseline Regression RMSLE for sku_id 222765: 5909.7969051432565
Baseline Regression RMSLE for sku_id 223153: 8406.616246076936
Baseline Regression RMSLE for sku_id 223245: 9059.852459486452
Baseline Regression RMSLE for sku_id 245338: 4072.9502501409115
Baseline Regression RMSLE for sku_id 245387: 3038.59

Okay good, I think we will be happy using all our engineered features, In the next section we hyperparameter tune some candidate models using TSCV

# <span style="color: purple; background-color: None; font-size: 36px; font-weight: bold; font-style: italic;"> Tuning and Evaluation of Candidate Models  </span>

<span style="color:#003366; background-color:#F0F8FF; font-size: 26px; font-weight: bold; font-style: italic;"> Random Forest Regressor  </span>

To increase the speed of tuning, I use a randomized search with Optuna library instead of an exhaustive GridSearch:

In [45]:
optuna.logging.set_verbosity(optuna.logging.WARNING) # Suppress Optuna's detailed trial output
best_params = dict()
for sku_id, feature_list in final_feature_sets.items():
   
    train_sku = train[train['sku_id'] == sku_id].copy().sort_values('week')
    
    X_sku = train_sku[feature_list]
    y_sku = np.log1p(train_sku['units_sold'])

    
    print(f"  Starting Optuna hyperparameter search for SKU {sku_id}...")
    def objective(trial):
        params = {
            'n_estimators': trial.suggest_categorical('n_estimators', [200, 400]),
            'max_features': trial.suggest_categorical('max_features', ['sqrt', 0.8]),
            'min_samples_split': trial.suggest_int('min_samples_split', 5, 10),
            'min_samples_leaf': trial.suggest_int('min_samples_leaf', 1, 4),
            'random_state': random_seed,
            'n_jobs': -1
        }
        
        if trial.suggest_categorical('unlimited_depth', [True, False]):
            params['max_depth'] = None
        else:
            params['max_depth'] = 10

        model = RandomForestRegressor(**params)
        
        tscv = TimeSeriesSplit(n_splits=3)
        fold_errors = []
        for train_idx, val_idx in tscv.split(X_sku):
            X_train, X_val = X_sku.iloc[train_idx], X_sku.iloc[val_idx]
            y_train, y_val = y_sku.iloc[train_idx], y_sku.iloc[val_idx]
            
            model.fit(X_train, y_train)
            preds = model.predict(X_val)
            
            fold_err = RMSLE(np.expm1(y_val), np.expm1(preds))
            fold_errors.append(fold_err)
            
        return np.mean(fold_errors)

    
    study = optuna.create_study(direction='minimize')
    study.optimize(objective, n_trials=20) 
    
    best_params[sku_id] = study.best_params
    if best_params[sku_id].pop('unlimited_depth'):
        best_params[sku_id]['max_depth'] = None
    else:
        best_params[sku_id]['max_depth'] = 10

    print(f"  Best params found: {best_params[sku_id]}")

  Starting Optuna hyperparameter search for SKU 216233...
  Best params found: {'n_estimators': 400, 'max_features': 'sqrt', 'min_samples_split': 10, 'min_samples_leaf': 4, 'max_depth': None}
  Starting Optuna hyperparameter search for SKU 216418...
  Best params found: {'n_estimators': 400, 'max_features': 'sqrt', 'min_samples_split': 9, 'min_samples_leaf': 1, 'max_depth': 10}
  Starting Optuna hyperparameter search for SKU 216419...
  Best params found: {'n_estimators': 200, 'max_features': 'sqrt', 'min_samples_split': 6, 'min_samples_leaf': 1, 'max_depth': 10}
  Starting Optuna hyperparameter search for SKU 216425...
  Best params found: {'n_estimators': 400, 'max_features': 'sqrt', 'min_samples_split': 9, 'min_samples_leaf': 1, 'max_depth': None}
  Starting Optuna hyperparameter search for SKU 217217...
  Best params found: {'n_estimators': 400, 'max_features': 'sqrt', 'min_samples_split': 8, 'min_samples_leaf': 1, 'max_depth': None}
  Starting Optuna hyperparameter search for SKU 

In [46]:
err = dict()
for sku_id, feature_list in final_feature_sets.items():
    
    train_sku = train[train['sku_id'] == sku_id].copy().sort_values('week')
    
    X_sku = train_sku[feature_list]
    y_sku = np.log1p(train_sku['units_sold'])

    print("  Starting final validation with Time Series Cross-Validation...")
    tscv_for_validation = TimeSeriesSplit(n_splits=4)
    fold_errors = []
    bp = best_params[sku_id]
    best_model = RandomForestRegressor(random_state=random_seed, n_jobs=-1, **bp)

    for i, (train_idx, val_idx) in enumerate(tscv_for_validation.split(X_sku)):
        Xtrain, Xval = X_sku.iloc[train_idx], X_sku.iloc[val_idx]
        ytrain, yval = y_sku.iloc[train_idx], y_sku.iloc[val_idx]
        
        best_model.fit(Xtrain, ytrain)
        y_pred = best_model.predict(Xval)
        fold_err = RMSLE(np.expm1(yval), np.expm1(y_pred))
        fold_errors.append(fold_err)
        print(f"    Fold {i+1} RMSLE: {fold_err:.4f}")

    validation_error = np.mean(fold_errors)
    err[sku_id] = validation_error
    print(f"  TSCV RMSLE for sku_id {sku_id}: {validation_error:.4f}")

print(f"\nAverage TSCV RMSLE across all SKU's: {np.mean(list(err.values())):.4f}")

  Starting final validation with Time Series Cross-Validation...
    Fold 1 RMSLE: 4526.4311
    Fold 2 RMSLE: 3410.9478
    Fold 3 RMSLE: 4152.4353
    Fold 4 RMSLE: 3739.3529
  TSCV RMSLE for sku_id 216233: 3957.2918
  Starting final validation with Time Series Cross-Validation...
    Fold 1 RMSLE: 7136.3053
    Fold 2 RMSLE: 9348.8365
    Fold 3 RMSLE: 8944.6522
    Fold 4 RMSLE: 8704.1089
  TSCV RMSLE for sku_id 216418: 8533.4757
  Starting final validation with Time Series Cross-Validation...
    Fold 1 RMSLE: 7286.8276
    Fold 2 RMSLE: 7961.9385
    Fold 3 RMSLE: 6068.5166
    Fold 4 RMSLE: 5940.1992
  TSCV RMSLE for sku_id 216419: 6814.3704
  Starting final validation with Time Series Cross-Validation...
    Fold 1 RMSLE: 3217.6173
    Fold 2 RMSLE: 2825.4411
    Fold 3 RMSLE: 2841.0567
    Fold 4 RMSLE: 2661.0474
  TSCV RMSLE for sku_id 216425: 2886.2906
  Starting final validation with Time Series Cross-Validation...
    Fold 1 RMSLE: 2215.5775
    Fold 2 RMSLE: 2384.7922
   

Awesome! Now we have to keep in mind this **RMSLE** value **3473** for the ***RF Regressor*** Model. We proceed to take the same steps to calculate the value for other candidate models in the next two sections. The one which would have the lowest RMSLE will be selected as the champion model.

<span style="color:#003366; background-color:#F0F8FF; font-size: 26px; font-weight: bold; font-style: italic;"> Light Gradient Boosting Machine (LGBM)  </span>

In [47]:
# for sku_id, feature_list in final_feature_sets.items():

#     # LGBM handles categorical features and does not need encoding:
#     feature_list.remove('store_encoded')
#     feature_list += ['store_id']

In [48]:
# optuna.logging.set_verbosity(optuna.logging.WARNING) # Suppress Optuna's detailed trial output

# best_params = dict()
# for sku_id, feature_list in tqdm(final_feature_sets.items(), desc="Tuning model for all SKUs"):
    
#     train_sku = train[train['sku_id'] == sku_id].copy().sort_values('week')
    
#     categorical_features = ['store_id', 'is_featured_sku', 'is_display_sku', 'is_holiday']
#     categorical_features = [f for f in categorical_features if f in feature_list]
    
#     X_sku = train_sku[feature_list]
#     y_sku = np.log1p(train_sku['units_sold'])
    
#     #Xtrain, Xval, ytrain, yval = train_test_split(X_sku, y_sku, test_size=0.2, shuffle=False)
    
#     def objective(trial):
#         params = {
#             'objective': 'regression_l1', 'random_state': random_seed, 'n_jobs': -1, 'verbose': -1,
#             'n_estimators': trial.suggest_int('n_estimators', 200, 1000),
#             'learning_rate': trial.suggest_float('learning_rate', 0.01, 0.05),
#             'num_leaves': trial.suggest_int('num_leaves', 20, 50),
#             'colsample_bytree': trial.suggest_float('colsample_bytree', 0.7, 1.0),
#             'subsample': trial.suggest_float('subsample', 0.7, 1.0),
#             'reg_alpha': trial.suggest_float('reg_alpha', 0.0, 1.0),
#             'reg_lambda': trial.suggest_float('reg_lambda', 0.0, 1.0),
#         }

#         tscv = TimeSeriesSplit(n_splits=3)
#         fold_errors = []
#         for train_idx, val_idx in tscv.split(X_sku):
#             X_train, X_val = X_sku.iloc[train_idx], X_sku.iloc[val_idx]
#             y_train, y_val = y_sku.iloc[train_idx], y_sku.iloc[val_idx]

#             model = lgb.LGBMRegressor(**params)
            
#             model.fit(X_train, y_train,
#                   eval_set=[(X_val, y_val)],
#                   callbacks=[lgb.early_stopping(50, verbose=False)],
#                   categorical_feature=categorical_features)
#             preds = model.predict(X_val)
            
#             fold_err = RMSLE(np.expm1(y_val), np.expm1(preds))
#             fold_errors.append(fold_err)
            
#         return np.mean(fold_errors)
        

#     study = optuna.create_study(direction='minimize')
#     study.optimize(objective, n_trials=50) 
    
#     best_params[sku_id] = study.best_params

In [49]:
# err = dict()
# for sku_id, feature_list in final_feature_sets.items():
    
#     train_sku = train[train['sku_id'] == sku_id].copy().sort_values('week')
    
#     X_sku = train_sku[feature_list]
#     y_sku = np.log1p(train_sku['units_sold'])

#     tscv_for_validation = TimeSeriesSplit(n_splits=4)
#     fold_errors = []
#     bp = best_params[sku_id]
#     best_model = LGBMRegressor(objective='regression_l1', random_state=random_seed, n_jobs=-1, verbose=-1, **bp)

#     for i, (train_idx, val_idx) in enumerate(tscv_for_validation.split(X_sku)):
#         Xtrain_fold, Xval_fold = X_sku.iloc[train_idx], X_sku.iloc[val_idx]
#         ytrain_fold, yval_fold = y_sku.iloc[train_idx], y_sku.iloc[val_idx]
        
#         best_model.fit(Xtrain_fold, ytrain_fold, categorical_feature=categorical_features)
#         y_pred = best_model.predict(Xval_fold)
#         fold_err = RMSLE(np.expm1(yval_fold), np.expm1(y_pred))
#         print(f"    Fold {i+1} RMSLE: {fold_err:.4f}")
#         fold_errors.append(fold_err)

#     validation_error = np.mean(fold_errors)
#     err[sku_id] = validation_error
#     print(f"  TSCV RMSLE for sku_id {sku_id}: {validation_error:.4f}")

# print(f"\nAverage TSCV RMSLE across all SKU's: {np.mean(list(err.values())):.4f}")

The RMSLE of ***LGBM*** is **3794** > 3473 (RMSLE of RF Regressor), so for now, the chamion model may be RF Regressor. But it seems strange as the lightGBM model is a stronger model in most tasks. The reason we might not be getting a good lgbm error could be its higher sensitivity to its hyperparameters compared to that of RF to its own. So I run the tuning and TSCV error calculation again, this time with learning rate search space between 0.01 and 0.05 (instead of 1) and increase the number of optuna trials from 20 to 50. If it still has higher error, we proclaim RF as the champion! I did this and it got a little bit better but still 3741 which is higher than RF Regressor Error. So yes, RF Regressor is the champion model.

XGBM is another possible candidate model, which can be tuned and validated similar to LGBM. I might add that in future versions. For now we stay with RF Regressor and predict on the test set in the next section.

# <span style="color: purple; background-color: None; font-size: 36px; font-weight: bold; font-style: italic;"> Recursive Forecasting Loop </span>

In [50]:
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 13860 entries, 150150 to 164009
Data columns (total 80 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   record_ID            13860 non-null  int64         
 1   week                 13860 non-null  datetime64[ns]
 2   store_id             13860 non-null  int64         
 3   sku_id               13860 non-null  int64         
 4   total_price          13860 non-null  float64       
 5   base_price           13860 non-null  float64       
 6   is_featured_sku      13860 non-null  int64         
 7   is_display_sku       13860 non-null  int64         
 8   units_sold           13860 non-null  float64       
 9   diff                 13860 non-null  float64       
 10  relative_diff_total  13860 non-null  float64       
 11  relative_diff_base   13860 non-null  float64       
 12  weekend_date         13860 non-null  datetime64[ns]
 13  year                 1386

We have to drop the null columns becasue if we don't when we are creating those columns for the test df rows, pandas will create wrong new column names, instead of overwriting them.

In [51]:
test_cleaned = test.drop(columns=['lag_1_weeks', 'lag_2_weeks', 'lag_3_weeks', 'lag_4_weeks', 'lag_5_weeks', 'lag_8_weeks', 'lag_9_weeks', 'lag_10_weeks', 'lag_11_weeks', 'lag_12_weeks', 'lag_13_weeks', 'lag_17_weeks', 'lag_19_weeks', 'lag_20_weeks', 'lag_22_weeks', 'lag_23_weeks', 'lag_24_weeks', 'lag_25_weeks', 'lag_26_weeks', 'lag_28_weeks', 'lag_33_weeks', 'lag_34_weeks', 'lag_35_weeks', 'lag_36_weeks', 'lag_37_weeks', 'lag_38_weeks', 'lag_39_weeks', 'lag_40_weeks', 'lag_41_weeks', 'lag_42_weeks', 'lag_43_weeks', 'lag_44_weeks', 'lag_47_weeks', 'lag_48_weeks', 'lag_49_weeks', 'lag_50_weeks', 'lag_51_weeks', 'lag_52_weeks', 'lag_53_weeks', 'lag_54_weeks', 'lag_55_weeks', 'MA_2_weeks', 'MA_3_weeks', 'MA_4_weeks', 'MA_5_weeks', 'MA_6_weeks', 'MA_1_weeks'])

Since, our lag and moving average features for prediction weeks need to be created as we make predictions for each week, we need to runa recursive forecasting loop where the predictions of each week are added to the history dataframe to create the features of following weeks:

In [52]:
trained_models = {}
all_predictions = []

for sku_id, feature_list in final_feature_sets.items():
    
    train_sku = train[train['sku_id'] == sku_id].copy().sort_values('week')
    X_sku = train_sku[feature_list]
    y_sku = np.log1p(train_sku['units_sold'])

    #Retrain on full data for this SKU with the best parameters
    bp = best_params[sku_id]
    final_model = RandomForestRegressor(random_state=random_seed, n_jobs=-1, **bp)
    final_model.fit(X_sku, y_sku)
    trained_models[sku_id] = final_model
    print(f"  Final model for SKU {sku_id} trained.")

    print(f"  Starting recursive forecast...")
    history_df = train_sku.copy()
    test_cleaned_sku = test_cleaned[test_cleaned['sku_id'] == sku_id].copy()
    prediction_weeks = sorted(test_cleaned_sku['week'].unique())

    lags_to_create = [int(f.split('_')[1]) for f in feature_list if f.startswith('lag_')]
    windows_to_create = [int(f.split('_')[1]) for f in feature_list if f.startswith('MA_')]
    store_windows_to_create = [26]
    
    sku_weekly_predictions = []
    for week in prediction_weeks:
        
        current_week_df = test_cleaned_sku[test_cleaned_sku['week'] == week].copy()
        
        lag_features_df = create_lag_features(current_week_df, lags_to_create, history=history_df)

        ma_features_df = create_moving_average_features(current_week_df, windows_to_create, history=history_df)
    
        store_ma_features_df = create_moving_average_features_store(current_week_df, windows=store_windows_to_create, history=history_df)
    
        lag_cols_to_keep = ['record_ID'] + [f'lag_{lag}_weeks' for lag in lags_to_create]
        lag_features = lag_features_df[lag_cols_to_keep]
        
        ma_cols_to_keep = ['record_ID'] + [f'MA_{w}_weeks' for w in windows_to_create]
        ma_features = ma_features_df[ma_cols_to_keep]
        
        store_ma_cols_to_keep = ['record_ID'] + [f'store_moving_avg_{w}_weeks' for w in store_windows_to_create]
        store_ma_features = store_ma_features_df[store_ma_cols_to_keep]
    
        current_week_featured = current_week_df.merge(lag_features, on='record_ID', how='left')
        current_week_featured = current_week_featured.merge(ma_features, on='record_ID', how='left')
        current_week_featured = current_week_featured.merge(store_ma_features, on='record_ID', how='left')

        X_pred = current_week_featured[feature_list]
        log_preds = final_model.predict(X_pred)
        preds = np.expm1(log_preds)
        preds[preds < 0] = 0
        
        current_week_featured['units_sold'] = preds
        history_df = pd.concat([history_df, current_week_featured], ignore_index=True)
        sku_weekly_predictions.append(current_week_featured[['record_ID', 'week', 'sku_id', 'store_id', 'units_sold']])

    if sku_weekly_predictions:
        all_predictions.append(pd.concat(sku_weekly_predictions))

sub = pd.DataFrame(None, columns = ['record_ID', 'week', 'sku_id', 'store_id', 'units_sold'])
sub = pd.concat(all_predictions, ignore_index=True)
sub.sort_values(by=['record_ID']).to_csv('final_preds.csv', index=False)

  Final model for SKU 216233 trained.
  Starting recursive forecast...
  Final model for SKU 216418 trained.
  Starting recursive forecast...
  Final model for SKU 216419 trained.
  Starting recursive forecast...
  Final model for SKU 216425 trained.
  Starting recursive forecast...
  Final model for SKU 217217 trained.
  Starting recursive forecast...
  Final model for SKU 217390 trained.
  Starting recursive forecast...
  Final model for SKU 217777 trained.
  Starting recursive forecast...
  Final model for SKU 219009 trained.
  Starting recursive forecast...
  Final model for SKU 219029 trained.
  Starting recursive forecast...
  Final model for SKU 219844 trained.
  Starting recursive forecast...
  Final model for SKU 222087 trained.
  Starting recursive forecast...
  Final model for SKU 222765 trained.
  Starting recursive forecast...
  Final model for SKU 223153 trained.
  Starting recursive forecast...
  Final model for SKU 223245 trained.
  Starting recursive forecast...
  Fina

# <span style="color: purple; background-color: None; font-size: 36px; font-weight: bold; font-style: italic;"> Visualizations </span>

<span style="color:#003366; background-color:#F0F8FF; font-size: 26px; font-weight: bold; font-style: italic;"> Feature Importance </span>

In [53]:
all_feature_importances = []

for sku_id, model in trained_models.items():

    feature_list = final_feature_sets[sku_id]

    importance_df = pd.DataFrame({
        'Feature': feature_list,
        'Importance': model.feature_importances_
    })

    importance_df = importance_df.sort_values(by='Importance', ascending=False).reset_index(drop=True)

    importance_df['SKU_ID'] = sku_id
    
    all_feature_importances.append(importance_df)

combined_importances = pd.concat(all_feature_importances, ignore_index=True)

for sku_id in sorted(combined_importances['SKU_ID'].unique()):

    title = f"<h3>Feature Importances for SKU: {sku_id}</h3>"
    display(HTML(title))

    sku_df = combined_importances[combined_importances['SKU_ID'] == sku_id].drop('SKU_ID', axis=1)

    html_table = sku_df.to_html(index=False, float_format='{:.4f}'.format)
    display(HTML(html_table))

    print("\n" + "="*50 + "\n")

<span style="color:#003366; background-color:#F0F8FF; font-size: 26px; font-weight: bold; font-style: italic;"> Demand Plotting </span>

In [54]:
df = pd.read_csv('final_preds.csv')

# Specify the SKU and Store ID you want to visualize
sku_id_to_filter = 216419
store_id_to_filter = 8023

filtered_df = df[(df['sku_id'] == sku_id_to_filter) & (df['store_id'] == store_id_to_filter)].copy()

filtered_df['units_sold'] = np.ceil(filtered_df['units_sold']).astype(int)

fig = px.bar(
    filtered_df,
    x='week',
    y='units_sold',
    title=f'Weekly Demand for SKU {sku_id_to_filter} at Store {store_id_to_filter}',
    labels={'week': 'Week', 'units_sold': 'Units Sold'},
    template='plotly_white'
)

fig.update_layout(
    xaxis_title="Week",
    yaxis_title="Demand",
    font=dict(
        family="Courier New, monospace",
        size=12,
        color="#7f7f7f"
    )
)

fig.show()